Why are validation generations from epoch 5 and 95 are the same?

# Import libraries 

In [4]:
import sys
sys.path.insert(0, '../')

import IPython.display as ipd

from audiocraft.models import encodec, loaders, builders
from audiocraft.utils import utils
import omegaconf
import torch
import os
import random
import json
random.seed(3)

/home/karlos/Documents/workspace/venv/music/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# Load Model

In [5]:
musicgen_model_name = 'facebook/musicgen-small'

#Loading Encodec model
pkg = loaders.load_compression_model_ckpt(musicgen_model_name)
cfg = omegaconf.OmegaConf.create(pkg['xp.cfg'])

kwargs = utils.dict_from_config(getattr(cfg, 'encodec'))

encoder_name = kwargs.pop('autoencoder')
quantizer_name = kwargs.pop('quantizer')

encoder, decoder = builders.get_encodec_autoencoder(encoder_name, cfg)
quantizer = builders.get_quantizer(quantizer_name, cfg, encoder.dimension)
frame_rate = kwargs['sample_rate'] // encoder.hop_length
renormalize = kwargs.pop('renormalize', False)
kwargs.pop('renorm', None), type(quantizer), frame_rate
model = encodec.EncodecModel(encoder, decoder, quantizer,
                    frame_rate=frame_rate, renormalize=renormalize, **kwargs)
model.load_state_dict(pkg['best_state'])
model = model.eval()

/home/karlos/Documents/workspace/venv/music/lib/python3.10/site-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


# Listen generations

In [6]:
# Epoch 5
file1 = "/home/karlos/Documents/workspace/proj/music/trained_models/v0_11_apr20/samples/15/noinput_22073afff2444484870a16f3df44dcd4.pt"

# Epoch 95
file2 = "/home/karlos/Documents/workspace/proj/music/trained_models/v0_11_apr20/samples/95/noinput_4bc8489007bd4094bacaed8ea1153780.pt"

In [10]:
encoded_generation1 = torch.load(file1)
with open(file1[:-3] + '.json') as j:
    original_input1 = json.load(j)['conditioning']['condition']
    print(f'Original Input: {original_input1}, Filename: {file1}')
# decode and listen
melody_waveform_reconstructed1 = model.decode(encoded_generation1.unsqueeze(0), None)
ipd.display(ipd.Audio(melody_waveform_reconstructed[0].detach().numpy(), rate=kwargs['sample_rate']))

Original Input: One Hour Duduk Meditation_109, Filename: /home/karlos/Documents/workspace/proj/music/trained_models/v0_11_apr20/samples/15/noinput_22073afff2444484870a16f3df44dcd4.pt


In [11]:
encoded_generation2 = torch.load(file2)
with open(file2[:-3] + '.json') as j:
    original_input2 = json.load(j)['conditioning']['condition']
    print(f'Original Input: {original_input2}, Filename: {file2}')
# decode and listen
melody_waveform_reconstructed2 = model.decode(encoded_generation2.unsqueeze(0), None)
ipd.display(ipd.Audio(melody_waveform_reconstructed[0].detach().numpy(), rate=kwargs['sample_rate']))

Original Input: One Hour Duduk Meditation_109, Filename: /home/karlos/Documents/workspace/proj/music/trained_models/v0_11_apr20/samples/95/noinput_4bc8489007bd4094bacaed8ea1153780.pt


In [12]:
encoded_generation1

tensor([[1318,  354, 1554,  ..., 1104,  441, 1525],
        [1478, 2000, 1596,  ..., 1514, 1600, 1938],
        [1073, 1931, 1677,  ..., 1204, 1895,  991],
        [1801, 1801, 1151,  ..., 1628,  475,  176]])

In [13]:
encoded_generation2

tensor([[1318,  354, 1554,  ..., 1104,  441, 1525],
        [1478, 2000, 1596,  ..., 1514, 1600, 1938],
        [1073, 1931, 1677,  ..., 1204, 1895,  991],
        [1801, 1801, 1151,  ..., 1628,  475,  176]])

In [17]:
(encoded_generation1 != encoded_generation2).sum()

tensor(0)